# Step 1. Setting up an environment for work.

In [637]:
import pandas as pd
import plotly.express as px
import seaborn as sns
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import statistics
import requests
from io import StringIO
pd.options.plotting.backend = "plotly"

In [638]:
file_id = '1R7je4__doBwjsGn071dFWqtt_J5DpqO4'

download_url = f'https://drive.google.com/uc?export=download&id={file_id}'

response = requests.get(download_url)

if response.status_code == 200:
    with open('image.jpg', 'wb') as f:
        f.write(response.content)

    kick = pd.read_csv('image.jpg')
else:
    print('Failed to get file. HTTP status code:', response.status_code)
df = kick.copy(deep=True)

# Step 2. Data preprocessing.

## 2.1. Checking if the dataframe has any empty cells.





In [639]:
df.isnull().values.any()

False

## 2.2. There is no need for the "ID" column, since it wouldn't give any useful information for my research. Getting rid of it.

In [640]:
df.head()

ID                                               Name  \
0  1860890148  Grace Jones Does Not Give A F$#% T-Shirt (limi...   
1   709707365                     CRYSTAL ANTLERS UNTITLED MOVIE   
2  1703704063                                drawing for dollars   
3      727286                       Offline Wikipedia iPhone app   
4  1622952265                                         Pantshirts   

       Category   Subcategory        Country             Launched    Deadline  \
0       Fashion       Fashion  United States  2009-04-21 21:02:48  2009-05-31   
1  Film & Video        Shorts  United States  2009-04-23 00:07:53  2009-07-20   
2           Art  Illustration  United States  2009-04-24 21:52:03  2009-05-03   
3    Technology      Software  United States  2009-04-25 17:36:21  2009-07-14   
4       Fashion       Fashion  United States  2009-04-27 14:10:39  2009-05-26   

    Goal  Pledged  Backers       State  
0   1000      625       30      Failed  
1  80000       22        3      Failed  
2     20       35        3  Successful  
3     99      145       25  Successful  
4   1900      387       10      Failed

In [641]:
df.drop('ID', axis=1, inplace=True)
df.head()


Name      Category  \
0  Grace Jones Does Not Give A F$#% T-Shirt (limi...       Fashion   
1                     CRYSTAL ANTLERS UNTITLED MOVIE  Film & Video   
2                                drawing for dollars           Art   
3                       Offline Wikipedia iPhone app    Technology   
4                                         Pantshirts       Fashion   

    Subcategory        Country             Launched    Deadline   Goal  \
0       Fashion  United States  2009-04-21 21:02:48  2009-05-31   1000   
1        Shorts  United States  2009-04-23 00:07:53  2009-07-20  80000   
2  Illustration  United States  2009-04-24 21:52:03  2009-05-03     20   
3      Software  United States  2009-04-25 17:36:21  2009-07-14     99   
4       Fashion  United States  2009-04-27 14:10:39  2009-05-26   1900   

   Pledged  Backers       State  
0      625       30      Failed  
1       22        3      Failed  
2       35        3  Successful  
3      145       25  Successful  
4      387       10      Failed

## 2.3. In the column "State" we can see five different types of values. I am not interested in canceled, live and suspended projects, because they have nothing to do with startups success rate. That's why I delete all these projects from the dataframe.

In [642]:
fig = px.bar(df['State'].value_counts(),
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='State',
                  yaxis_title='Number of projects',
                  title='Project state types',
                  width=600,
                  showlegend=False)
fig.show()

In [643]:
df = df[df['State'].str.contains("Successful|Failed")]
df = df.reset_index(drop=True)

## 2.4. Checking the dataframe for the duplicates.

In [644]:
print(len(df[df.duplicated()]))

0


## 2.5. Checking for the columns which are not very useful, that is the ones which contain >90% same values.

In [645]:
rowNum = len(df)
lowInfoColumns = []
for c in df.columns:
  counts = df[c].value_counts()
  most = (counts/rowNum).iloc[0]

  if most > 0.9:
    lowInfoColumns.append(c)
print(lowInfoColumns)

[]


## 2.6. Looking on these bar charts, we can ensure that there is no deviation in data, such as having the same names in different registers, typos, etc.

In [646]:
fig = px.bar(df['Category'].value_counts(),
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='Category',
                  yaxis_title='Number of projects',
                  title='Project categories',
                  width=600,
                  showlegend=False)
fig.show()

In [647]:
fig = px.bar(df['Subcategory'].value_counts(),
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='Subcategory',
                  yaxis_title='Number of projects',
                  title='Project subcategories',
                  width=1300,
                  showlegend=False)
fig.show()

In [648]:
fig = px.bar(df['Country'].value_counts(),
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='Country',
                  yaxis_title='Number of projects',
                  title='Project by countries',
                  width=600,
                  showlegend=False)
fig.show()

## 2.7. By simply finding the sum, we can ensure that we have only numbers in the columns "Goal", "Pledged", "Backers", because no errors occur.

In [649]:
sumsDf = pd.DataFrame([sum(df['Goal']), sum(df['Pledged']), sum(df['Backers'])])
sumsDf.index = ['Goal','Pledged','Backers']

fig = px.bar(sumsDf,
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='Column',
                  yaxis_title='Sum',
                  title='Numerical sums',
                  width=600, showlegend=False)
fig.show()


## 2.8. As we can see the dtypes of "Launched" and "Deadline" are object, so I convert them to datetime.

In [650]:
df['Launched'].info()
print('\n')
df['Deadline'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 331462 entries, 0 to 331461
Series name: Launched
Non-Null Count   Dtype 
--------------   ----- 
331462 non-null  object
dtypes: object(1)
memory usage: 2.5+ MB


<class 'pandas.core.series.Series'>
RangeIndex: 331462 entries, 0 to 331461
Series name: Deadline
Non-Null Count   Dtype 
--------------   ----- 
331462 non-null  object
dtypes: object(1)
memory usage: 2.5+ MB


In [651]:
df['Deadline'] = pd.to_datetime(df['Deadline'])
df['Launched'] = pd.to_datetime(df['Launched'])

In [652]:
df['Launched'].info()
print('\n')
df['Deadline'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 331462 entries, 0 to 331461
Series name: Launched
Non-Null Count   Dtype         
--------------   -----         
331462 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 2.5 MB


<class 'pandas.core.series.Series'>
RangeIndex: 331462 entries, 0 to 331461
Series name: Deadline
Non-Null Count   Dtype         
--------------   -----         
331462 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 2.5 MB


## 2.9. Cleaning out "broken" rows.

### This dataframe has columns "Backers" and "Pledged". And it is completely obvious, that if the number of backers is 0, then the amount of pledged money cannot be more than 0. Let's see if this rule is observed in this dataset.

In [653]:
for i in range(len(df)):
  if df['Pledged'][i] > 0 and df['Backers'][i] == 0:
    print(df.loc[[i]])
    df.drop(i, inplace=True)
df = df.reset_index(drop=True)

               Name      Category  Subcategory        Country  \
4596  Sins Of A Son  Film & Video  Documentary  United States   

                Launched   Deadline  Goal  Pledged  Backers   State  
4596 2010-07-02 23:41:15 2010-09-04  3500        1        0  Failed  
             Name Category     Subcategory        Country            Launched  \
168481  iStandUp!   Design  Product Design  United States 2014-11-19 19:20:02   

         Deadline   Goal  Pledged  Backers   State  
168481 2014-12-31  50000      218        0  Failed  
                     Name      Category   Subcategory        Country  \
253159  The Falcon Fly By  Film & Video  Film & Video  United States   

                  Launched   Deadline  Goal  Pledged  Backers   State  
253159 2016-04-05 15:08:31 2016-06-04  5000        1        0  Failed  


# Step 3. Analyzing.

## 3.1. Numbers of kickstarter projects in different countries on a map.
 (some countries with small amount of projects launched are not presented)



In [654]:
project_country_counts = df['Country'].value_counts().reset_index()
project_country_counts.columns = ['Country', 'Count']

fig = px.choropleth(project_country_counts,
                    locations="Country",
                    locationmode="country names",
                    color="Count",
                    hover_name="Country",
                    projection="natural earth")

fig.update_layout(height=600,
                  width=800)
fig.show()


So, we have the most projects launched in North America. Also there were projects from Europe, UK, Australia and Japan. America exceeds other countries by many times. Also there are no countries with the required number in the middle of the range. We see only yellow and blue, no orange, red and purple.

## 3.2. Mean and median of goal and pledged amounts of money and backers.

In [655]:
mean_goal = round(df['Goal'].mean())
mean_pledged = round(df['Pledged'].mean())
mean_backers = round(df['Backers'].mean())
print(mean_goal, mean_pledged, mean_backers)

41523 9940 116


So, on average, people asked for about 41522 dollars for their project. And the mean of the amount of pledged money is about 9940 dollars. For the backers the number is about 116.

In [656]:
median_goal = df['Goal'].median()
median_pledged = df['Pledged'].median()
median_backers = df['Backers'].median()
median = pd.DataFrame({'Metric': ['Goal', 'Pledged', 'Backers'],
                       'Median': [median_goal, median_pledged, median_backers]})

As we can see, median values for these columns are 5000, 788 and 15 respectively.

In [657]:
newDf = pd.DataFrame({'name':['Goal', 'Pledged', ''],
                      'mean':[mean_goal, mean_pledged, mean_backers],
                      'median':[median_goal, median_pledged, median_backers]})

newDf.set_index('name', inplace=True)

fig = make_subplots(rows=1, cols=2,
                    specs=[[{'type':'bar'},
                            {'type':'bar'}]],
                    subplot_titles=('Goal and Pledged',
                                    'Backers'))

fig.add_trace(go.Bar(name='Mean',
                     x=newDf.index[:2],
                     y=newDf['mean'][:2],
                     marker_color='#2a8b00'),
               row=1, col=1)
fig.add_trace(go.Bar(name='Median',
                     x=newDf.index[:2],
                     y=newDf['median'][:2],
                     marker_color='#2a8b00'),
               row=1, col=1)

fig.add_trace(go.Bar(name='Mean',
                     x=newDf.index[2:],
                     y=newDf['mean'][2:],
                     marker_color='#2a8b00'),
               row=1, col=2)
fig.add_trace(go.Bar(name='Median',
                     x=newDf.index[2:],
                     y=newDf['median'][2:],
                     marker_color='#2a8b00'),
               row=1, col=2)

fig.update_layout(barmode='group',
                  title='Mean and median',
                  width=700,
                  showlegend=False)
fig.show()

In [658]:
std_goal = round(df['Goal'].std())
std_pledged = round(df['Pledged'].std())
std_backers = round(df['Backers'].std())
print(std_goal, std_pledged, std_backers)

1109284 96646 966


In [659]:
newDf = pd.DataFrame({'names':['Goal', 'Pledged', 'Backers'], 'std':[std_goal, std_pledged, std_backers]})
newDf.set_index('names', inplace=True)
import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Bar(name='Standard deviation',
                     x=newDf.index[:1],
                     y=newDf['std'][:1],
                     marker_color='#2a8b00'))

fig.add_trace(go.Bar(name='Standard deviation',
                     x=newDf.index[1:2],
                     y=newDf['std'][1:2],
                     marker_color='#2a8b00'))

fig.add_trace(go.Bar(name='Standard deviation',
                     x=newDf.index[2:],
                     y=newDf['std'][2:],
                     marker_color='#2a8b00'))

fig.update_layout(barmode='group',
                  title='Standard deviation',
                  width=600,
                  showlegend=False,
                  yaxis_type="log")
fig.show()

Standard deviations values are all relatively big, which means that these columns have high variability.

## 3.3. Projects general success rate.

In [660]:
px.pie(df, names='State',
       title='Startups current state',
       height=600, width=800, hole=.5,
       color_discrete_sequence=['#003f5c', '#ffa600']).show()

## 3.4. Success rate by year.

In [662]:
df['StateInt'] = df['State'].map({'Successful': 1, 'Failed': 0})

df_yearly_counts = df.groupby([df['Launched'].dt.year, 'StateInt'])['StateInt'].count()
df_yearly_counts = df_yearly_counts.unstack().fillna(0)
df_yearly_counts.columns = ['Failed', 'Successful']
df_yearly_counts['Total'] = df_yearly_counts['Failed'] + df_yearly_counts['Successful']


df_yearly_counts['SuccessPercentage'] = (df_yearly_counts['Successful'] / df_yearly_counts['Total']) * 100
df_yearly_counts['FailPercentage'] = (df_yearly_counts['Failed'] / df_yearly_counts['Total']) * 100

df_yearly_counts = df_yearly_counts.reset_index()

import plotly.graph_objects as go
import pandas as pd

data = df_yearly_counts


data['x'] = data['Total'].cumsum() - data['Total']


fig = go.Figure()


fig.add_trace(go.Bar(
    x=data['x'],
    y=data['SuccessPercentage'],
    width=data['Total'],
    name='Successful',
    marker_color='brown',
    offset=0
))


fig.add_trace(go.Bar(
    x=data['x'],
    y=data['FailPercentage'],
    width=data['Total'],
    name='Failed',
    marker_color='green',
    offset=0
))


fig.update_layout(
    title='Mekko Chart of Launch Success and Fail Percentage by Year',
    xaxis=dict(
        title='Total Launches',
        tickvals=data['x'] + data['Total']/2,
        ticktext=data['Launched']
    ),
    yaxis=dict(
        title='Percentage',
        tickformat='%',
    ),
    barmode='stack',
    barnorm='fraction',
    showlegend=True
)

# Show the figure
fig.show()


# Step 4. Hypothesis and research.

## Hypothesis.

### Assume that the amount of pledged money grew many times since 2009 to 2017. But is it because average "backer" on kickstarter gave more money to support a project? Or is it because in general the number of project and backers grew? Which of these two factors impact the result the most?

### My hypothesis is that the number of backers and projects matter the most.

## Research.

In [663]:
nums_by_years = pd.DataFrame()
nums_by_years['Backers'] = df.groupby(df['Launched'].dt.year)['Backers'].sum()
nums_by_years['Pledged'] = df.groupby(df['Launched'].dt.year)['Pledged'].sum()
nums_by_years['Average Backer Spent'] = nums_by_years['Pledged']/nums_by_years['Backers']

### Let's see how the amount of money pledged per year changed.

In [664]:
nums_by_years['Pledged'] = df.groupby(df['Launched'].dt.year)['Pledged'].sum()

fig = make_subplots(rows=1, cols=2,
                    subplot_titles=("Pledged",
                                    "Average backer spent"))

fig.add_trace(
    go.Bar(x=nums_by_years.index,
           y=nums_by_years['Pledged'],
           marker_color='#2a8b00'),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=nums_by_years.index,
           y=nums_by_years['Average Backer Spent'],
           marker_color='#2a8b00'),
    row=1, col=2
)

fig.update_layout(height=600,
                  width=900,
                  title_text="Numbers per year",
                  showlegend=False)
fig.update_xaxes(title_text="Year")
fig.update_yaxes(title_text="USD")

### Well, we see that both numbers did grow in general, but it is hard to tell how similar this growth is by just looking at it, so let's check the correlation.

In [665]:
avgbs = nums_by_years['Average Backer Spent']
plgd = nums_by_years['Pledged']
corr0 = plgd.corr(avgbs)
fig = go.Figure(data=[go.Pie(labels=['Success', 'Failure'],
                             values=[corr0, 1-corr0], hole=.3,
                             marker=dict(colors=['#003f5c', '#ffa600']))])

fig.update_layout(
    title='Dark - correlation between the growth rates',
    width=600,
    showlegend=False
)

### We do see a strong correlation. But this is not enough.

In [666]:
avgbs_growth_rate = avgbs[2017]/avgbs[2009] - 1
plgd_growth_rate = plgd[2017]/plgd[2009] - 1
growth_rate = pd.DataFrame({'Name':['Average backer spent', 'Pledged'],
                            'Value':[avgbs_growth_rate, plgd_growth_rate]})
growth_rate.set_index('Name', inplace=True)

fig = px.bar(growth_rate['Value'],
             color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='',
                  yaxis_title='',
                  title='Growth rate',
                  width=600,
                  showlegend=False,
                  yaxis=dict(type="log",
                             autorange=True,
                             tickvals=[1, 10, 100, 200]))
fig.show()


### Average backer spent grew by about 44% from 2009 to 2017, whereas the amount of pledged money per year grew more than 200 times! Difference is so big, I had to change the scale to be able to normally see the first bar. So, these are almost unrelated. What about the amounts of projects and backings?<sup>[1](#backings)</sup>
<a name="backings">1</a>: That is when 1 person gives money 1 time to 1 project.



###How the amount of projects, backings and pledged money grew over time.

In [ ]:
df['Cumulative Pledged'] = df['Pledged'].cumsum()
df['Number of backers'] = df['Backers'].cumsum()
df['Number of projects'] = range(1, len(df) + 1)
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, subplot_titles=("Cumulative Pledged, USD", "Number of backers", "Number of projects"))

fig.add_trace(go.Scatter(x=df['Launched'],
                         y=df['Cumulative Pledged'],
                         mode='lines', name='Total pledged'), row=3, col=1)
fig.add_trace(go.Scatter(x=df['Launched'], y=df['Number of backers'], mode='lines', name='Number of backings'), row=2, col=1)
fig.add_trace(go.Scatter(x=df['Launched'], y=df['Number of projects'], mode='lines', name='Number of projects'), row=1, col=1)

fig.update_layout(height=800, width=600, title_text="Kickstarter stats over time", xaxis_title="Time", yaxis_title="")

fig.show()


### After certain point, approximately in 2011, the number of projects on Kickstarter started growing almost linearly and at the same speed, and about a year later same thing happened to the number of backers and the total amount of pledged money.



###We can easily see a great correlation, but let's compute it.

In [ ]:
corr1 = statistics.mean([
    df['Cumulative Pledged'].corr(df['Number of backers']),
    df['Number of projects'].corr(df['Number of backers']),
    df['Number of projects'].corr(df['Cumulative Pledged'])])

fig = go.Figure(data=[go.Pie(values=[corr1, 1-corr1],
                             hole=.3,
                             marker=dict(colors=['#003f5c', '#ffa600']))])

fig.update_layout(
    title='Dark - correlation between the growth rates',
    width=600,
    showlegend=False
)

### The correlation rate is extremely high, almost a full coincidence. Let's dig deeper.

In [ ]:
df_2010_2017 = df[df['Launched'].dt.year.isin([2010, 2017])].groupby(df['Launched'].dt.year).first()
plgd_diff = df_2010_2017['Cumulative Pledged'][2017]/df_2010_2017['Cumulative Pledged'][2010] - 1
back_diff = df_2010_2017['Number of backers'][2017]/df_2010_2017['Number of backers'][2010] - 1
proj_diff = df_2010_2017['Number of projects'][2017]/df_2010_2017['Number of projects'][2010] - 1
diff = pd.DataFrame({'Value':[plgd_diff,
                              back_diff,
                              proj_diff],
                     'Name': ['Pledged',
                              'Backings',
                              'Projects']}).set_index('Name')

fig = px.scatter(diff, x=diff.index, y='Value', size='Value',
                 color_discrete_sequence=['#2a8b00'])

fig.update_layout(xaxis_title='',
                  yaxis_title='times',
                  title='Difference between 2010 and 2017',
                  width=600,
                  showlegend=False)
fig.show()


### Amount of money pledged in the beggining of 2017 was 945 times more than in 2010. The number of backers grew more than 750 times. The number of projects increased by 243 times.
 *I take values for the beginnings of 2010 and 2017, because in the beginning of 2009 there is not enough info to talk about the growth rates, and in the end of 2017 there was still many live projects, which were removed from this dataframe.
### These numbers look very nice, we see that the the amount of pledged money grew almost as many times as the number of backings. And the difference with the 'number of projects' column is not nearly as small as it was with the average backer spent.


## Conclusion.

### I can conclude that my hypothesis was right, because with the number of backers and project we can see a stronger correlation and less difference in growth rates, than with the averge backer spent.